In [19]:
import json
import requests
import pandas as pd
import numpy as np
from io import StringIO
from requests.auth import HTTPBasicAuth
from datetime import datetime, timedelta
import matplotlib.pyplot as plt
import plotly.express as px
import meteomatics.api as api

In [ ]:
# PEGAR OS DADOS DIRETO DO WEBSERVICE: 

In [10]:
wildfire_data = pd.read_csv('J1_VIIRS_C2_USA_contiguous_and_Hawaii_7d.csv')

In [11]:
wildfire_data

latitude  longitude  bright_ti4  scan  track    acq_date  acq_time  \
0      48.18765  -64.92101       303.5  0.39   0.36  2020-09-24       624   
1      20.86389  -75.77474       308.3  0.39   0.36  2020-09-24       636   
2      21.43146  -87.82571       297.0  0.62   0.71  2020-09-24       636   
3      18.92953  -70.35270       303.1  0.56   0.43  2020-09-24       636   
4      18.40117  -70.03501       314.3  0.40   0.44  2020-09-24       636   
...         ...        ...         ...   ...    ...         ...       ...   
35467  46.38675 -116.05692       340.8  0.44   0.38  2020-10-01      2042   
35468  46.39091 -116.05217       350.2  0.44   0.38  2020-10-01      2042   
35469  46.83700 -115.83714       337.4  0.45   0.39  2020-10-01      2042   
35470  46.49352 -120.48605       350.2  0.39   0.36  2020-10-01      2042   
35471  46.48974 -120.53156       339.1  0.39   0.36  2020-10-01      2042   

       satellite confidence version  bright_ti5   frp daynight  
0              1    nominal  2.0NRT       284.0   0.8        N  
1              1    nominal  2.0NRT       291.6   0.8        N  
2              1    nominal  2.0NRT       272.3   1.4        N  
3              1    nominal  2.0NRT       284.6   0.6        N  
4              1    nominal  2.0NRT       291.5   2.1        N  
...          ...        ...     ...         ...   ...      ...  
35467          1    nominal  2.0NRT       304.0  39.3        D  
35468          1    nominal  2.0NRT       293.9  11.3        D  
35469          1    nominal  2.0NRT       278.0  31.4        D  
35470          1    nominal  2.0NRT       300.7  24.2        D  
35471          1    nominal  2.0NRT       305.4   2.8        D  

[35472 rows x 13 columns]

In [12]:
min_data = wildfire_data['acq_date'].min()

In [13]:
wildfire_data['acq_time'] = wildfire_data['acq_time'].astype('str').str.zfill(4)

In [14]:
wildfire_data['seconds'] = wildfire_data.apply(lambda x: (datetime.strptime(x['acq_date'], '%Y-%m-%d')-datetime.strptime(min_data, '%Y-%m-%d')).total_seconds()+(datetime.strptime(x['acq_time'], '%H%M')-datetime(1900, 1, 1)).total_seconds(), axis=1)

In [15]:
wildfire_data['seconds'] = wildfire_data['seconds']/(3600*24)

In [16]:
px.set_mapbox_access_token('pk.eyJ1IjoiZXVyb3BpbzEyMyIsImEiOiJja2ZyZmd2bWEwdXlwMnJydmpvanl2eGJyIn0.eB5mSN6pgC0Hpx2UjhG1Jw')

In [17]:
fig = px.scatter_mapbox(wildfire_data, lat="latitude", lon="longitude", color="seconds",
                  color_continuous_scale=px.colors.sequential.YlOrRd, size_max=15, zoom=10)
fig.show()

In [19]:
grid_rows = 3600
grid_cols = 7200
fire_grid = np.zeros((3600, 7200))

In [26]:
wildfire_data

latitude  longitude  bright_ti4  scan  track    acq_date acq_time  \
0      48.18765  -64.92101       303.5  0.39   0.36  2020-09-24     0624   
1      20.86389  -75.77474       308.3  0.39   0.36  2020-09-24     0636   
2      21.43146  -87.82571       297.0  0.62   0.71  2020-09-24     0636   
3      18.92953  -70.35270       303.1  0.56   0.43  2020-09-24     0636   
4      18.40117  -70.03501       314.3  0.40   0.44  2020-09-24     0636   
...         ...        ...         ...   ...    ...         ...      ...   
35467  46.38675 -116.05692       340.8  0.44   0.38  2020-10-01     2042   
35468  46.39091 -116.05217       350.2  0.44   0.38  2020-10-01     2042   
35469  46.83700 -115.83714       337.4  0.45   0.39  2020-10-01     2042   
35470  46.49352 -120.48605       350.2  0.39   0.36  2020-10-01     2042   
35471  46.48974 -120.53156       339.1  0.39   0.36  2020-10-01     2042   

       satellite confidence version  bright_ti5   frp daynight   seconds  
0              1    nominal  2.0NRT       284.0   0.8        N  0.266667  
1              1    nominal  2.0NRT       291.6   0.8        N  0.275000  
2              1    nominal  2.0NRT       272.3   1.4        N  0.275000  
3              1    nominal  2.0NRT       284.6   0.6        N  0.275000  
4              1    nominal  2.0NRT       291.5   2.1        N  0.275000  
...          ...        ...     ...         ...   ...      ...       ...  
35467          1    nominal  2.0NRT       304.0  39.3        D  7.862500  
35468          1    nominal  2.0NRT       293.9  11.3        D  7.862500  
35469          1    nominal  2.0NRT       278.0  31.4        D  7.862500  
35470          1    nominal  2.0NRT       300.7  24.2        D  7.862500  
35471          1    nominal  2.0NRT       305.4   2.8        D  7.862500  

[35472 rows x 14 columns]

In [35]:
for i in range(wildfire_data.shape[0]):
    lat, long = wildfire_data.iloc[[i]]['latitude'].values[0], wildfire_data.iloc[[i]]['longitude'].values[0]
    row_index = int(round(((lat + 90) / 180) * grid_rows))
    column_index = int(round(((long + 180) / 360) * grid_cols))
    fire_grid[row_index][column_index] = 1

In [20]:
r = requests.get('https://api.meteomatics.com/2020-10-01T18Z,2020-10-02T18ZPT2H:PT20M/relative_humidity_2m:p,wind_speed_10m:kmh,wind_dir_10m:d/47.4245,9.3767/csv?model=mix',
                 auth=HTTPBasicAuth('federaluniversityofpernambuco_lacerda',
                                    '9KxSd6DeBoPw3'))

In [21]:
TESTDATA = StringIO(r.text)
df = pd.read_csv(TESTDATA, sep=";")

In [22]:
df

validdate  relative_humidity_2m:p  wind_speed_10m:kmh  \
0  2020-10-01T18:00:00Z                    83.9                13.2   
1  2020-10-02T18:00:00Z                    40.5                37.0   
2  2020-10-02T18:20:00Z                    38.7                37.0   
3  2020-10-02T18:40:00Z                    37.6                47.2   
4  2020-10-02T19:00:00Z                    38.9                40.6   
5  2020-10-02T19:20:00Z                    38.7                33.1   
6  2020-10-02T19:40:00Z                    40.9                21.8   
7  2020-10-02T20:00:00Z                    39.8                32.0   

   wind_dir_10m:d  
0           221.5  
1           130.3  
2           122.3  
3           123.1  
4           135.4  
5           138.2  
6           127.5  
7           143.0

In [3]:
#"MCD12C1.A2019001.006.2020220162300.hdf"

In [11]:
import h5py
filename = "MCD12C1.A2019001.006.2020220162300.h5"

with h5py.File(filename, "r") as f:
    # List all groups
    print("Keys: %s" % f.keys())

    # Get the data
    data = f['Num_IGBP_Classes:MOD12C1']

Keys: <KeysViewHDF5 ['MOD12C1', 'Num_IGBP_Classes:MOD12C1', 'Num_LAI_FPAR_Classes:MOD12C1', 'Num_UMD_Classes:MOD12C1', 'XDim:MOD12C1', 'YDim:MOD12C1']>


In [12]:
f = h5py.File("MCD12C1.A2019001.006.2020220162300.h5", "r")

In [13]:
data = f['MOD12C1']['Data Fields']['Majority_Land_Cover_Type_1']

In [22]:
row_index = int(round(((8.024102 + 90) / 180) * 3600))
column_index = int(round(((-34.926335 + 180) / 360) * 7200))

In [23]:
row_index, column_index

(1960, 2901)

In [24]:
np_data = np.array(data)

In [25]:
np_data[np_data > 0] = 1

In [26]:
data[row_index][column_index]

13

In [ ]:
import plotly.graph_objects as go

fig = go.Figure(data=go.Heatmap(
                   z=np_data,
                   x=list(range(np_data.shape[0])),
                   y=list(range(np_data.shape[1]))))
fig.show()